In [61]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import re 
import spacy
from sklearn.feature_extraction.text import CountVectorizer
from datetime import datetime
from nltk.corpus import stopwords 
from nltk.tokenize import word_tokenize
from nltk.util import ngrams
from textblob import TextBlob
from nltk.util import ngrams
from vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer

data = pd.read_csv('comments_500k_201903_comments_500k_201903.csv')

In [62]:
data.shape

(500000, 7)

In [63]:
print(data.info())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 500000 entries, 0 to 499999
Data columns (total 7 columns):
parent_id       500000 non-null object
subreddit_id    500000 non-null object
subreddit       500000 non-null object
created_utc     500000 non-null int64
author          500000 non-null object
score           500000 non-null int64
body            499996 non-null object
dtypes: int64(2), object(5)
memory usage: 26.7+ MB
None


In [433]:
data.sample(10)

parent_id subreddit_id           subreddit  created_utc  \
315558   t3_avwavh     t5_2xrd1           gtaonline   1551399999   
114361  t1_eiqcy83     t5_2zgb7   shittysuperpowers   1552851398   
248970  t1_ejr7gfb     t5_2qhx4             Fitness   1553982371   
468634   t3_b5adq0     t5_2stl8               Smite   1553519063   
254355   t3_aximfm     t5_2s64c        dresdenfiles   1551778043   
336874   t3_ayv0uk     t5_2r8hf               leafs   1552079202   
466044  t1_ehlqgbx     t5_2v6vs  Achievement_Hunter   1551504709   
302328  t1_ehx0oji     t5_2x1rn   im14andthisisdeep   1551888853   
368280   t3_b7hxk5     t5_2y76k       FitAndNatural   1554000329   
72980   t1_eje7pre     t5_2vg7t        pettyrevenge   1553573694   

                    author  score  \
315558         elliot_sufc     27   
114361     scooterdooter62     57   
248970  FletchForPresident     21   
468634     Stevethebeast08     -4   
254355      ThePirateStorm     21   
336874     BuffaloSobbers1     30   
466044         Classix1331     -5   
302328         Bassknight9     25   
368280           HikerGimp     35   
72980           SmellMyHat    139   

                                                     body  
315558  Apart from money glitches. It’s almost as if t...  
114361  I'm no doctor, but I'm pretty sure you still h...  
248970  "Complete abstinence is easier than perfect mo...  
468634  I'm defintely going to be playing more hunters...  
254355  I listed the Dresden Files as my favourite ser...  
336874  I don't get it. Everybody who's supposed to pu...  
466044  I'm still not a big fan of Jeremy. I like him ...  
302328  I believe it is about leaving toxic relationsh...  
368280                https://instagram.com/thamires.pazz  
72980                                         Cheers babe

### change created_utc

In [36]:
data.created_utc[1]

1551689919

In [37]:
parsed_date = datetime.utcfromtimestamp(data.created_utc[1])
parsed_date

datetime.datetime(2019, 3, 4, 8, 58, 39)

In [38]:
data.created_utc.apply(lambda x: datetime.utcfromtimestamp(x))

0        2019-03-24 09:33:58
1        2019-03-04 08:58:39
2        2019-03-08 09:46:13
3        2019-03-18 11:07:27
4        2019-03-09 09:24:56
5        2019-03-05 12:02:43
6        2019-03-17 13:36:46
7        2019-03-30 14:11:37
8        2019-03-26 12:21:12
9        2019-03-22 12:05:15
10       2019-03-16 15:05:47
11       2019-03-06 13:25:07
12       2019-03-03 15:28:06
13       2019-03-14 23:49:53
14       2019-03-08 00:07:16
15       2019-03-08 00:11:02
16       2019-03-27 00:14:07
17       2019-03-15 13:48:40
18       2019-03-02 12:08:35
19       2019-03-12 11:21:54
20       2019-03-08 09:47:53
21       2019-03-04 10:51:46
22       2019-03-06 13:06:57
23       2019-03-26 12:09:52
24       2019-03-07 17:41:27
25       2019-03-05 09:29:40
26       2019-03-03 16:21:56
27       2019-03-12 10:41:29
28       2019-03-08 12:49:29
29       2019-03-15 11:03:04
                 ...        
499970   2019-03-18 16:45:05
499971   2019-03-01 02:20:22
499972   2019-03-21 10:39:27
499973   2019-

### Group by Subreddit 

In [39]:
group = (data.groupby('subreddit')['body'].apply(lambda x: ','.join(set(x.dropna()))).reset_index())
group.head(8)

subreddit                                               body
0           1000ccplus  Sorry, but that is Steve Tyler with tits,Cute ...
1           100thieves  I don't think any real fans would doubt the ef...
2          100yearsago  Probably not. Something that long and thin wou...
3              11foot8  they need a P.A. system that kicks in whenever...
4  1200isfineIGUESSugh  Just eat,. it's one day! you don't have the be...
5          1200isjerky  Slightly related, but I got really pissed off ...
6         1200isplenty  Added agar to my shopping list haha,1/2 cup Ko...
7     1200isplentyketo  I went low carb a year ago (not keto). My HDL ...

In [437]:
print (data.groupby('subreddit')['body'].nunique().sort_values(ascending=False).head())
# print (pd.DataFrame.from_records(group_subreddit.values.tolist()).stack().value_counts())
# print (df.groupby('param')['group'].nunique())
# group_by.head()

subreddit
ChapoTrapHouse     4500
todayilearned      4311
SquaredCircle      3905
rupaulsdragrace    3709
hockey             3639
Name: body, dtype: int64


In [41]:
data[data.subreddit=="100yearsago"]

parent_id subreddit_id    subreddit  created_utc              author  \
140649  t1_eiphhqb     t5_2y3jq  100yearsago   1552798843  bad_at_hearthstone   
238666   t3_b24h6m     t5_2y3jq  100yearsago   1552824597         michaelnoir   

        score                                               body  
140649     15  Probably not. Something that long and thin wou...  
238666     20  \n* Battle of Bolshie Ozerki – A Red Army brig...

### Test removing stop words with NLTK & counting each word 

In [42]:
data.body[1000]

"They're perfectly smart creatures. They just can't come up with anything *new*."

In [43]:
data.body[1000] = re.sub(r'\W+', ' ', data.body[1000].lower())
data.body[1000]

/Users/juliekim/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


'they re perfectly smart creatures they just can t come up with anything new '

In [44]:
ex_sentence = data.body[1000]
stop_words = set(stopwords.words('english'))
word_tokens = word_tokenize(ex_sentence)

filtered_sentence = [w for w in word_tokens if not w in stop_words]
filtered_sentence = []
for w in word_tokens:
    if w not in stop_words:
        filtered_sentence.append(w)
print(word_tokens)
print(filtered_sentence)


['they', 're', 'perfectly', 'smart', 'creatures', 'they', 'just', 'can', 't', 'come', 'up', 'with', 'anything', 'new']
['perfectly', 'smart', 'creatures', 'come', 'anything', 'new']


In [45]:
words = filtered_sentence
counts = dict()
for word in words:
    if word in counts:
        counts[word] += 1
    else:
        counts[word] = 1
print(counts)

{'perfectly': 1, 'smart': 1, 'creatures': 1, 'come': 1, 'anything': 1, 'new': 1}


### clean comments function 

In [46]:
def clean(sentence):
    sentence = re.sub(r'\W+', ' ', sentence.lower())
    return sentence

In [47]:
clean_data = group.body.apply(lambda x: clean(x))
clean_df = pd.DataFrame(clean_data)
clean_df.head(5)

body
0  sorry but that is steve tyler with tits cute b...
1  i don t think any real fans would doubt the ef...
2  probably not something that long and thin woul...
3  they need a p a system that kicks in whenever ...
4  just eat it s one day you don t have the be so...

### remove stop words function 

In [48]:
def token_func(sentence):
    stop_words = set(stopwords.words('english'))
    word_tokens = word_tokenize(sentence)
    filtered_sentence = [w for w in word_tokens if not w in stop_words] 
  
    filtered_sentence = [] 
  
    for w in word_tokens: 
        if w not in stop_words: 
            filtered_sentence.append(w)
            
    return filtered_sentence

### word count function 


In [49]:
def word_count(sentence):
    sentence = re.sub(r'\W+', ' ', sentence.lower())
    counts = dict()
    words = filtered_sentence

    for word in words:
        if word in counts:
            counts[word] += 1

        else:
            counts[word] = 1
    return counts


### entity 

In [67]:
data.body[1200]

'[Atlanta United fans replying to banter threads circa 2019 colorized](https://i.imgur.com/p6BAGhe.jpg)'

In [122]:
import spacy
nlp = spacy.load('en_core_web_sm')
doc = nlp(data.body[110])
for ent in doc.ents:
    print(ent.text, ent.label_)

Dachdecker PERSON
Mechatroniker PERSON
Straßenbauer ORG


In [71]:
nlp = spacy.load('en_core_web_sm')
doc = nlp(data.body[1200])
for ent in doc:
    print(ent.text, ent.pos_, ent.dep_)

[ PUNCT punct
Atlanta PROPN compound
United PROPN compound
fans NOUN ROOT
replying VERB acl
to PART prep
banter VERB compound
threads NOUN compound
circa NOUN pobj
2019 NUM nummod
colorized](https://i.imgur.com PROPN npadvmod
/ SYM punct
p6BAGhe.jpg ADP punct
) PUNCT punct


### entity count

In [195]:
group = (data.groupby('subreddit')['body'].apply(lambda x: ','.join(set(x.dropna()))).reset_index())

In [145]:
from collections import Counter
nlp = spacy.load('en')
doc2 = nlp(group.body[112])
# all tokens that arent stop words or punctuations
words = [token.text for token in doc2 if token.is_stop != True and token.is_punct != True]

# noun tokens that arent stop words or punctuations
nouns = [token.text for token in doc2 if token.is_stop != True and token.is_punct != True and token.pos_ == "NNP"]

# ten most common tokens
word_freq = Counter(words)
common_words = word_freq.most_common(10)

# ten most common noun tokens
noun_freq = Counter(nouns)
common_nouns = noun_freq.most_common(10)

In [146]:
common_words

[('\n\n', 7),
 (' ', 5),
 ('use', 3),
 ('ice', 3),
 ('week', 3),
 ('minutes', 2),
 ('twice', 2),
 ('hour', 2),
 ('prior', 2),
 ('sauna', 2)]

In [148]:
common_nouns

[('CBD', 2),
 ('MEDICAL', 2),
 ('ADVICE', 2),
 ('Youtube', 1),
 ('Hemochromatosis', 1),
 ('RBM3', 1),
 ('ALS', 1),
 ('QUESTIONS', 1),
 ('SEEK', 1),
 ('PROFESSIONAL', 1)]

In [133]:
docp = nlp(group.body[112])
for token in docp:
    print(token.text, token.pos_, token.tag_, token.dep_,
            token.shape_, token.is_alpha, token.is_stop)

use VERB VB ROOT xxx True False
Youtube PROPN NNP dobj Xxxxx True False
to PART TO aux xx True True
learn VERB VB xcomp xxxx True False
how ADV WRB advmod xxx True True
to PART TO aux xx True True
use VERB VB xcomp xxx True False
an DET DT det xx True True
ice NOUN NN compound xxx True False
chest NOUN NN dobj xxxx True False
as ADP IN prep xx True True
an DET DT det xx True True
ice NOUN NN compound xxx True False
bath NOUN NN pobj xxxx True False
. PUNCT . punct . False False
Work VERB VB ROOT Xxxx True False
your DET PRP$ poss xxxx True True
way NOUN NN dobj xxx True False
to ADP IN prep xx True True
6C/43F NUM CD pobj dX/ddX False False
for ADP IN prep xxx True True
6 NUM CD nummod d False False
minutes NOUN NNS pobj xxxx True False
, PUNCT , punct , False False
twice ADV RB advmod xxxx True False
a DET DT det x True True
week NOUN NN npadvmod xxxx True False
. PUNCT . punct . False False
  SPACE _SP    False False
Take VERB VB ROOT Xxxx True True
melatonin NOUN NN dobj xxxx True F

In [134]:
nlp = spacy.load('en_core_web_sm')
docs = nlp(group.body[112])
counts = dict()
for ent in docs:
    if ent.text in counts:
        counts[ent.text] += 1
    else:
        counts[ent.text] = 1
print(counts)      

{'use': 3, 'Youtube': 1, 'to': 6, 'learn': 1, 'how': 1, 'an': 2, 'ice': 3, 'chest': 1, 'as': 5, 'bath': 1, '.': 17, 'Work': 1, 'your': 3, 'way': 1, '6C/43F': 1, 'for': 3, '6': 1, 'minutes': 2, ',': 13, 'twice': 2, 'a': 7, 'week': 3, ' ': 5, 'Take': 1, 'melatonin': 1, 'hour': 2, 'prior': 2, 'the': 3, 'batch': 1, 'recommend': 1, 'blue': 1, 'tooth': 1, 'headphones': 1, 'and': 3, 'spotify': 1, 'blast': 1, 'high': 1, 'energy': 1, 'song': 1, 'on': 1, 'repeat': 1, '\n\n': 7, 'four': 1, 'days': 1, 'dry': 1, 'sauna': 2, '80C/174F': 1, '20': 1, 'take': 3, 'restveratrol': 1, 'one': 1, '(': 1, 'do': 2, 'not': 4, 'phone': 1, 'or': 1, 'bluetooth': 1, 'into': 1, ')': 1, 'get': 1, 'DNA': 1, 'check': 1, 'see': 1, 'if': 1, 'you': 1, 'genes': 1, 'Hemochromatosis': 1, 'If': 1, 'so': 1, 'spoonful': 2, 'of': 3, 'coconut': 1, 'oil': 2, 'tumeric': 1, 'lots': 1, 'ground': 1, 'pepper-': 1, 'quite': 1, 'often': 1, '1': 1, '-': 2, '3': 1, 'times': 1, 'per': 2, 'day': 2, 'skip': 1, 'I': 1, "'m": 1, 'sure': 1, 'CBD

In [97]:
# doc = nlp(group.body)
for i in range(len(group.body)):
    for ent in nlp(group.body[i]).ents:
        print(ent.text, ent.label_)

Steve Tyler PERSON
Cute ORG
summer DATE
summer DATE
TL ORG
the end of the day DATE
6th ORDINAL
Showed PERSON
’m ORG
Fero.,I PERSON
about 2 CARDINAL
Jungler PERSON
Drafts PERSON
this weekend DATE
last year DATE
this week DATE
500$ MONEY
three CARDINAL
half CARDINAL
600 to 800 CARDINAL
Allied ORG
Bolshie Ozerki FAC
Onega PERSON
Russia GPE
60 to 80 CARDINAL
French NORP
White Russian NORP
67th ORDINAL
68th DATE
69th ORDINAL
the British Army ORG
214th Brigades ORG
The Oklahoma Senate ORG
the Miami School of Mines ORG
Miami GPE
Oklahoma GPE
Northeastern Oklahoma A&amp;M College ORG
The Penang Chinese Girls' High School ORG
George Town GPE
Penang GPE
Malaysia GPE
Náutico Marcílio Dias PERSON
Itajaí GPE
Brazil GPE
1919 DATE
Vancouver GPE
Canadian National Railway ORG
Berlin GPE
1,200 CARDINAL
3 March DATE
Canadian NORP
Railways and Canals ORG
the Grand Trunk Railway ORG
Sergey Rakhmaninov PERSON
45 CARDINAL
nine CARDINAL
the American Piano Co. ORG
Ampico ORG
first ORDINAL
Baltic States GPE
Ukr

Native American NORP
Indian NORP
half CARDINAL
Koreaboo GPE
Japan GPE
99.7 CARDINAL
23 CARDINAL
only one CARDINAL
Native American NORP
the United Kingdom GPE
one CARDINAL
23andme CARDINAL
23andme CARDINAL
OP.,Is CARDINAL
’s ORG
Sadly PERSON
two CARDINAL
two CARDINAL
two CARDINAL
two CARDINAL
’m PERSON
One night TIME
a week prior DATE
90% PERCENT
European NORP
10% PERCENT
African NORP
90% PERCENT
Asian NORP
10% PERCENT
European NORP
French NORP
Nigerian-Kenyan NORP
at least 98 CARDINAL
European NORP
African NORP
1-2% PERCENT
more than 1 CARDINAL
2% PERCENT
3 CARDINAL
European NORP
African NORP
Asian NORP
Central Asian NORP
Afghan NORP
South Asian NORP
almost 70% PERCENT
85.5% PERCENT
Central &amp ORG
South LOC
two CARDINAL
Indian NORP
0 CARDINAL
Indian NORP
Pashtuns PERSON
Kabul GPE
Afghanistan GPE
half CARDINAL
Pakistan GPE
Pashtun PERSON
Balochi GPE
Tajikistan LOC
South Asian NORP
Central Asia LOC
reference](http://i.imgur.com/XlujjdW.jpg ORG
Spanish NORP
Spain GPE
North African NORP


2 CARDINAL
41 CARDINAL
Primaris GPE
35 CARDINAL
Primaris GPE
70 MONEY
65 MONEY
75 CARDINAL
3 CARDINAL
60 CARDINAL
3 CARDINAL
50 CARDINAL
3 CARDINAL
15 CARDINAL
IIRC Lorgar PERSON
Fulgrim ORG
Lion PERSON
Caliban ORG
Chogoris PERSON
40 CARDINAL
the Rogue Trader ORG
Goto PERSON
Goto PERSON
Just Bad WORK_OF_ART
Horus Heresy LOC
Abyss ORG
Las PERSON
Space Marine PERSON
Act V PRODUCT
Herman Melville PERSON
John PERSON
Russ PERSON
Horus PERSON
Dreadnought ORG
Captain Malcharion PERSON
Raguel the Suffer PERSON
the Ninth Legion ORG
second ORDINAL
one CARDINAL
Imperial ORG
Martyred Lady PERSON
Bloody Rose ORG
Ebon Chalice ORG
Last Prioress ORG
Argent ORG
Shroud.,I'm PRODUCT
The Phoenician’s WORK_OF_ART
half CARDINAL
Fulgrim’s ORG
Guilliman’s ORG
Fulgrim’s ORG
Guilliman ORG
Dark Imperium FAC
Mary Sueness PERSON
Necrons PERSON
AdMech ORG
Three CARDINAL
Lorgar GPE
1 CARDINAL
13 CARDINAL
one CARDINAL
Institutionalized ORG
Galaxy GPE
Pysker PERSON
Ecclesiarch PERSON
Warmaster PERSON
Imperial Knight O

FUN ORG
MOS ORG
MAKIN PERSON
A TRUKK OUTTA SKULLS WORK_OF_ART
YA TRAIWED OFF AT DA END DERE WORK_OF_ART
GIT ORG
EN NORP
YOO GIT PERSON
YA STUPID GIT WORK_OF_ART
NEKRONZ ORG
NEKRONZ ORG
ORKS ORKS ORKS ORKS ORKS ORKS ORKS ORKS OOOOOORRRRRKKSSSSS LAW
IZZIT POSSIBUL TA LERN DIS KNOW-WOTZ?,CUZ IT'Z ORG
40,000 CARDINAL
ORKS ORG
EXAMPLE ORG
KNOWIN ORG
GO ORG
JAYK ORG
WHAT'RE YOO WEARIN WORK_OF_ART
JAYK ORG
Khakis PERSON
GROT ORG
One CARDINAL
RT GPE
LOT ORG
Roll20 ORG
PvP ORG
GM ORG
one CARDINAL
two CARDINAL
GM ORG
Kinda PERSON
Giants ORG
Chiefs ORG
Beckham PERSON
Beckham ORG
DJ Reed’s ORG
YPC ORG
NFL 2k5 PRODUCT
Metcalf PRODUCT
6th ORDINAL
6th ORDINAL
DE ORG
17th DATE
WR ORG
two CARDINAL
Murray PERSON
ILB ORG
’s ORG
Andy PERSON
56 CARDINAL
one CARDINAL
Pittsburgh GPE
Jesus Christ PERSON
2 CARDINAL
the last 10 years DATE
DK ORG
Brown PERSON
second ORDINAL
Jimmie IR Ward PERSON
Allen PERSON
40 CARDINAL
4.62 CARDINAL
118 CARDINAL
DNP ORG
7.15 CARDINAL
4.23 CARDINAL
28 CARDINAL
40 CARDINAL
4.79 C

77 DATE
Kyoto GPE
’m PERSON
Itsuki - Eats ORG
Itsuki GPE
Fuutarou PERSON
FBI ORG
Shield Hero PERSON
’m PERSON
Nino NORP
Miku LOC
Yotsuba GPE
Whoaaa ORG
Nice.,Miku ORG
Fuutarou PERSON
Yotsuba GPE
Mista GPE
Kyoto GPE
Nino NORP
Fuu PERSON
Miku PERSON
Itsuki ORG
Yotsuba GPE
Yotsuba GPE
Nino NORP
Kryptonite NORP
Nino NORP
Submarine PERSON
Yotsuba GPE
Nino NORP
Miku NORP
Ichika NORP
Miku PERSON
each week DATE
Miku Church ORG
Miku Church ORG
Miku ORG
Fuutarou PERSON
Itsuki PERSON
YotsubaxHappiness ORG
Ichika - Cool ORG
Nino NORP
Miku - Plays NORP
Yotsuba - Goes PERSON
Itsuki - Eats ORG
Gridman ORG
Basara Toujou PERSON
Miku NORP
masterpiece(NSFW)](https://www.reddit.com ORG
MikuNakano ORG
MikuNakano ORG
Japanese NORP
Miku NORP
Takeda ORG
Artist ORG
Nino NORP
Fuutarou ORG
Yotsuba GPE
5 CARDINAL
fourth ORDINAL
5 CARDINAL
Yotsuba GPE
4th ORDINAL
one CARDINAL
Papakano PERSON
Itsuki GPE
Kyoto GPE
two CARDINAL
1 CARDINAL
’m PERSON
2 CARDINAL
one CARDINAL
Yotsuba GPE
Miku PERSON
END.,Nino Gang R E P 

...

Germany GPE
Chimken PERSON
Moose PERSON
Can’t PERSON
200 dollars MONEY
ADHD ORG
second ORDINAL
Darling GPE
Kamina PERSON
Simon PERSON
Rossiu GPE
Sinners NORP
the season DATE
a second season DATE
Hitler PERSON
Naofumi PERSON
Kusuo PERSON
one CARDINAL
4 CARDINAL
Southern Mindanao PERSON
Mizushima PERSON
Tarou PERSON
One CARDINAL
Rising GPE
Filo PERSON
half CARDINAL
Spear Hero PERSON
Shield Hero PERSON
Zero CARDINAL
first ORDINAL
Stuff ORG
Bruno PERSON
Pizza

Mista accusing ORG
Fugo ORG
600 milion CARDINAL
Fugo ORG
Narancia PERSON
Mista GPE
Formaggio PERSON
Narancia PERSON
Bruno PERSON
Alessandro Nannini PERSON
Mista NORP
Fugo NORP
Boss ORG
Trish

Turtle ORG
Abbacchio PERSON
Giorno PERSON
Grateful Dead PERSON
Beach Boy PERSON
Narancia PERSON
Giorno PERSON
Narancia PERSON
Narancia PERSON
Giorno PERSON
Venetian NORP
Giorno PERSON
Abbacchio PERSON
Trish NORP
Narancia PERSON
Bruce Lee PERSON
2 CARDINAL
Bruno PERSON
Narancia PERSON
Abbacchio PERSON
Giorno PERSON
Try Kissmanga PERSON
Araki PERS

13+ year DATE
10 year olds DATE
Tattoo ORG
one CARDINAL
Kaguya PERSON
first ORDINAL
non-Japanese NORP
Soviet NORP
F-86D Dog Sabre PERSON
#* MONEY
STAND ORG
ゴゴゴゴゴゴゴゴゴゴゴ*,I ORG
two CARDINAL
first ORDINAL
Newt PERSON
Grindelwald PERSON
Cowboy Bebop PRODUCT
Code Geass PERSON
8/10s PERSON
10/10s CARDINAL
a ton QUANTITY
two CARDINAL
Dororo PERSON
Dororo PERSON
S2**](#sleepingcutie NORP
Dumbbells**](#wow CARDINAL
Sasuga Doga Kobo PERSON
13 CARDINAL
two CARDINAL
1's](https://i.imgur.com CARDINAL
2015 DATE
Jump PERSON
Anime ORG
SoL ORG
Kineta GPE
Ranked ORG
Friday DATE
their day DATE
Monday DATE
votes!](https://imgur.com/MJZTMA3 ORG
Killua Again](https://imgur.com/SbAtK3H ORG
Today DATE
Nice GPE
Hayasaka PERSON
Akane Tsunemori ORG
Psycho Pass ORG
week DATE
Haibane Renmei WORK_OF_ART
Musical ORG
God PERSON
Doga Kobo PERSON
Kaguya-sama PERSON
8 CARDINAL
Japanese LANGUAGE
10 minutes TIME
2.5 CARDINAL
Hatchin PERSON
Hatchin PERSON
Hatchin PERSON
Michiko PERSON
South-America LOC
Tutu PERSON
two CARD

Katsuki Bakugō PERSON
Klackson PERSON
Ochako Uraraka PERSON
Olivia Upper PERSON
Tabby Hopps PERSON
Momo Yaoyorozu PERSON
Mandy Yates PERSON
Minoru Mineta ORG
Sticky Mickey PERSON
Ritsu ORG
Yuu PERSON
Ichigo PERSON
one CARDINAL
One CARDINAL
Japanese NORP
approximately 2 years DATE
Season 3 ORG
another 2 years DATE
Season 4 FAC
the next few years DATE
2 years DATE
months DATE
about season CARDINAL
3 CARDINAL
Summer 2022 DATE
2025 DATE
Season ORG
Absolute PERSON
Sakura PERSON
Rin PERSON
one CARDINAL
Season 2 FAC
2006 DATE
two minutes TIME
between 2006 to now DATE
8.71$ MONEY
monthly DATE
US GPE
Masterpiece PERSON
Kakyoin ORG
Araki PERSON
Phil PERSON
Phil PERSON
Eugeosexual PERSON
David Pro PERSON
two CARDINAL
Alicization ORG
KyoAni ORG
Violet Evergarden GPE
Kaguya-sama ORG
one CARDINAL
5 CARDINAL
3 CARDINAL
Sakura PERSON
C.C GPE
& ORG
Arisu LOC
ACTUALLY ORG
Reigen PERSON
Rim PERSON
Uprising.,I CARDINAL
DIO ORG
Hayasaka GPE
Hayasaka PERSON
Hayasaka](https://i.imgur.com/HcFxwQ3.jpg ORG
Kagu

Lmfao PERSON
overlooks decades DATE
Jim Crow PERSON
-Civil Rights Act LAW
Bill Clinton PERSON
some years DATE
second ORDINAL
Chuck Berry PERSON
ACDC ORG
Huey Lewis PERSON
80s DATE
’m PERSON
Amazon ORG
Guevara ORG
Castro PERSON
Castro PERSON
Cuba GPE
one CARDINAL
South America LOC
Castro PERSON
Cuba GPE
Guevara GPE
Cuba GPE
Guevara PERSON
Castro PERSON
US GPE
the early 1900's DATE
late night TIME
6 pounds QUANTITY
Google Patents ORG
Kemper ORG
system](https://patents.google.com ORG
US3922730A/en ORG
Diagram](https://patentimages.storage.googleapis.com/90/cf/ab/7d48a21d8640cf/US3922730-drawings-page-2.png ORG
10 CARDINAL
30 CARDINAL
41 CARDINAL
25 CARDINAL
43 CARDINAL
42 CARDINAL
43 CARDINAL
24 CARDINAL
25 CARDINAL
16 CARDINAL
20 CARDINAL
25 CARDINAL
35 CARDINAL
34 CARDINAL
36 CARDINAL
37 CARDINAL
11 CARDINAL
38 CARDINAL
25 CARDINAL
39 CARDINAL
36 CARDINAL
37 CARDINAL
38 CARDINAL
44 CARDINAL
25 CARDINAL
Autopilot ORG
million CARDINAL
Joseph Treeman PERSON
slaves?,I'm PERSON
ISP ORG
one d

KeyboardInterrupt: 

In [186]:
group.head()

subreddit                                               body
0           1000ccplus  Sorry, but that is Steve Tyler with tits,Cute ...
1           100thieves  I don't think any real fans would doubt the ef...
2          100yearsago  Probably not. Something that long and thin wou...
3              11foot8  they need a P.A. system that kicks in whenever...
4  1200isfineIGUESSugh  Just eat,. it's one day! you don't have the be...

In [198]:

# all tokens that arent stop words or punctuations
# words = [token.text for token in doc2 if token.is_stop != True and token.is_punct != True]
group['words'] = group['body'].map(lambda t:[token.text for token in nlp(t) if token.is_stop != True \
                                             and token.is_punct != True] )

# df = pd.concat([group['subreddit'], num_word['body']], axis=1, keys=['Subreddit', 'Values'])
# df['words'] = df['Values'].map(lambda t: sorted(t.items(), key = lambda x: x[1],reverse=True))



In [202]:
# noun tokens that arent stop words or punctuations
group['noun_words'] = group['body'].map(lambda t: [token.text for token in nlp(t) \
                                              if token.is_stop != True and token.is_punct != True \
                                              and token.pos_ == "PROPN"])
# word_freq = Counter(words)
# common_words = word_freq.most_common(10)

# counts = dict()
# for i in range(0,5):
#     for ent in nlp(group.body[i]).ents:
#         if ent.text in counts:
#             counts[ent.text] += 1
#         else:
#             counts[ent.text] = 1
# print(counts) 



In [200]:
group['count'] = group['words'].map(lambda t: Counter(t).most_common(10))

In [204]:
group['n_count'] = group['noun_words'].map(lambda t: Counter(t).most_common(10))

In [205]:
group.head()

subreddit                                               body  \
0           1000ccplus  Sorry, but that is Steve Tyler with tits,Cute ...   
1           100thieves  I don't think any real fans would doubt the ef...   
2          100yearsago  Probably not. Something that long and thin wou...   
3              11foot8  they need a P.A. system that kicks in whenever...   
4  1200isfineIGUESSugh  Just eat,. it's one day! you don't have the be...   

                                               words  \
0  [Sorry, Steve, Tyler, tits, Cute, old, thanks,...   
1  [think, real, fans, doubt, effort, going, jump...   
2  [Probably, long, thin, experience, massive, os...   
3  [need, P.A., system, kicks, somebody, gets, st...   
4  [eat, day, regimented, offense, kind, sounds, ...   

                                               count  \
0  [(Sorry, 1), (Steve, 1), (Tyler, 1), (tits, 1)...   
1  [(team, 10), ( , 5), (like, 4), (think, 3), (g...   
2  [(\n\n, 18), (March, 4), (Ozerki, 3), (French,...   
3  [(\n\n, 2), (bridge, 2), (need, 1), (P.A., 1),...   
4  [(\n\n, 15), (eat, 12), (day, 8), (food, 8), (...   

                                          noun_words  \
0                                     [Steve, Tyler]   
1  [’s, TL, Showed, ’s, Fero.,I, Jungler, Drafts,...   
2  [Bolshie, Ozerki, Red, Army, Allied, Bolshie, ...   
3                                    [P.A., day.,It]   
4  [Friday, Poptarts, WTF, ’s, metabolism.,I, hap...   

                                             n_count  
0                           [(Steve, 1), (Tyler, 1)]  
1  [(’s, 2), (TL, 1), (Showed, 1), (Fero.,I, 1), ...  
2  [(March, 4), (Ozerki, 3), (Oklahoma, 3), (Geor...  
3                          [(P.A., 1), (day.,It, 1)]  
4  [(’s, 4), (NSFW, 2), (REGARDLESS, 2), (Friday,...

In [572]:

myList=group[group.subreddit=="beauty"]['count']
for p in myList: 
    print(pd.DataFrame(p))


         0   1
0       \n  12
1     \n\n  10
2   person   7
3     good   5
4  amazing   4
5     like   3
6  quality   3
7  healthy   3
8     find   3
9     know   3


In [571]:
data.subreddit.sample(20)

262581                 gadgets
292757       therewasanattempt
487432                Animemes
226876          Showerthoughts
375328                  beauty
161494               2007scape
350390                  movies
471642                Landlord
96977          GlobalOffensive
253150             PartyParrot
188630            WayOfTheBern
105027        FireEmblemHeroes
369985    TeenMomOGandTeenMom2
153490                     MLS
412934      TwoBestFriendsPlay
82835            relationships
28594                  Gunners
43231                2007scape
117672      dankchristianmemes
477109           Documentaries
Name: subreddit, dtype: object

### top subreddits 

In [287]:
ordered_data = data.groupby('subreddit').agg('count').sort_values('body', ascending=False)


In [464]:
data.groupby('subreddit').agg('count').sort_values('body', ascending=False)

parent_id  subreddit_id  created_utc  author  score  \
subreddit                                                                   
ChapoTrapHouse             4673          4673         4673    4673   4673   
todayilearned              4511          4511         4511    4511   4511   
SquaredCircle              4065          4065         4065    4065   4065   
hockey                     3814          3814         3814    3814   3814   
rupaulsdragrace            3806          3806         3806    3806   3806   
pics                       3563          3563         3563    3563   3563   
movies                     3456          3456         3456    3456   3456   
MMA                        3305          3305         3305    3305   3305   
leagueoflegends            3266          3266         3266    3266   3266   
aww                        3203          3203         3203    3203   3203   
marvelstudios              2906          2906         2906    2906   2906   
videos                     2889          2889         2889    2889   2889   
CollegeBasketball          2881          2881         2881    2881   2881   
Animemes                   2872          2872         2872    2872   2872   
BlackPeopleTwitter         2754          2754         2754    2754   2754   
trashy                     2620          2620         2620    2620   2620   
PewdiepieSubmissions       2487          2487         2487    2487   2487   
formula1                   2411          2411         2411    2411   2411   
ukpolitics                 2402          2402         2402    2402   2402   
FortNiteBR                 2313          2313         2313    2313   2313   
thebachelor                2136          2136         2136    2136   2136   
relationship_advice        2084          2084         2084    2084   2084   
Showerthoughts             2028          2028         2028    2028   2028   
relationships              1999          1999         1999    1999   1999   
Games                      1938          1938         1938    1938   1938   
LivestreamFail             1927          1927         1927    1927   1927   
baseball                   1847          1847         1847    1847   1847   
PublicFreakout             1832          1832         1832    1832   1832   
interestingasfuck          1805          1805         1805    1805   1805   
europe                     1787          1787         1787    1787   1787   
...                         ...           ...          ...     ...    ...   
MLPIOS                        1             1            1       1      1   
MP5                           1             1            1       1      1   
hawwkey                       1             1            1       1      1   
MSLGame                       1             1            1       1      1   
Maps                          1             1            1       1      1   
headsdownbaseball             1             1            1       1      1   
ManjaroLinux                  1             1            1       1      1   
heartsofiron                  1             1            1       1      1   
Manitoba                      1             1            1       1      1   
ManifestNBC                   1             1            1       1      1   
hebrew                        1             1            1       1      1   
MangaCollectors               1             1            1       1      1   
Mandela_Effect                1             1            1       1      1   
hellblade                     1             1            1       1      1   
MandJTV                       1             1            1       1      1   
MalenaMorgan                  1             1            1       1      1   
hentaicaptions                1             1            1       1      1   
Malaphors                     1             1            1       1      1   
herbalism                     1             1            1       1      1   
MakeupEducation   

In [263]:
combined = pd.merge(group, ordered_data, on='subreddit').sort_values('parent_id', ascending=False). \
reset_index(drop=True)
combined 

subreddit                                             body_x  \
0         ChapoTrapHouse  fuck you fuck you fuck you fuck you fuck you!!...   
1          todayilearned  Earl had to die!,I tried but unfortunately the...   
2          SquaredCircle  I will say, him saying he doesn't think Roman ...   
3                 hockey  I rather they go for 12.,As a lifelong Habs fa...   
4        rupaulsdragrace  Is that a blunt im yodeling,Honestly it still ...   
5                   pics  Chiari friend! I had my spinal decompression s...   
6                 movies  I was in a movie, a bit early, sitting and wai...   
7                    MMA  Cowboy has such a beautiful headkick, probably...   
8        leagueoflegends  PLEASE REVERT THE WALKING ANIMATION FOR GOD SA...   
9                    aww  Don't feed the ones near the outskirt areas wh...   
10         marvelstudios  Not emotionally ready for that!,Virginity War,...   
11                videos  A year later a huge choir sang the song in a m...   
12     CollegeBasketball  I love comparing wieners,Yea, you right.  You ...   
13              Animemes  Oof. That Jotaro tho. . .,YOU TAKE THAT BACK! ...   
14    BlackPeopleTwitter  Fuck that, I’d just eat it. I ain’t trynna hav...   
15                trashy  Little cunts!\n\nGod you just want to sort the...   
16  PewdiepieSubmissions  Enough to to stop a 9 year old, not so sure ab...   
17              formula1  It's under a link to sky thing in first paragr...   
18            ukpolitics  I agree, Obama really shouldn't have intervene...   
19            FortNiteBR  im gay,Yes mods, do something and remove this ...   

                                                words  \
0   [fuck, fuck, fuck, fuck, fuck, you!!!1, ghoul,...   
1   [Earl, die!,I, tried, unfortunately, murder, m...   
2   [saying, think, Roman, chemo, pills, orally, w...   
3   [12.,As, lifelong, Habs, fan, grew, Ottawa, wo...   
4   [blunt, m, yodeling, Honestly, blows, mind, Al...   
5   [Chiari, friend, spinal, decompression, surger...   
6   [movie, bit, early, sitting, waiting, trailers...   
7   [Cowboy, beautiful, headkick, probably, second...   
8   [REVERT, WALKING, ANIMATION, GOD, SAKE, lettin...   
9   [feed, ones, near, outskirt, areas, tourists, ...   
10  [emotionally, ready, that!,Virginity, War, dif...   
11  [year, later, huge, choir, sang, song, mall, p...   
12  [love, comparing, wieners, Yea, right,  , got,...   
13  [Oof, Jotaro, tho, .,YOU, dual, wield, incest,...   
14  [Fuck, ’d, eat, ai, n’t, trynna, burger, fucke...   
15  [Little, cunts, \n\n, God, want, sort, jail, h...   
16  [stop, 9, year, old, sure, 88, million, 9, yea...   
17  [link, sky, thing, paragraph.,This, hardly, co...   
18  [agree, Obama, intervened, New, Labour, projec...   
19  [m, gay, Yes, mods, remove, post, \n\n, Seriou...   

                                                count  \
0   [(\n\n, 1523), (people, 634), (�, 606), (like,...   
1   [(\n\n, 1776), ( , 702), (like, 601), (people,...   
2   [(\n\n, 1135), (like, 555), (’s, 392), ( , 346...   
3   [(\n\n, 931), (like, 341), (’s, 288), ( , 279)...   
4   [(�, 1272), (\n\n, 704), (’s, 543), (like, 524...   
5   [(\n\n, 876), (like, 378), ( , 361), (people, ...   
6   [(\n\n, 1269), (movie, 769), (like, 617), ( , ...   
7   [(\n\n, 856), (fight, 493), (like, 421), (’s, ...   
8   [(\n\n, 1272), (game, 473), (like, 471), (team...   
9   [(�, 6952), (\n\n, 691), (like, 347), (’s, 276...   
10  [(\n\n, 840), (like, 455), (movie, 358), (’s, ...   
11  [(\n\n, 1031), ( , 478), (like, 416), (people,...   
12  [(\n\n, 602), (game, 278), (team, 248), ( , 24...   
13  [(⣿, 1160), (\n\n, 578), (�, 356), (like, 168)...   
14  [(\n\n, 695), (�, 438), (people, 398), (’s, 35...   
15  [(\n\n, 479), (people, 318), (like, 316), (’s,...   
16  [(�, 1670), (⣿, 967), (⠀, 782), (\n\n, 434), (...   
17  [(\n\n, 814), (like, 259), (race, 204), (car, ...   
18  [(\n\n, 1713), (people, 441), (\n, 424), (EU, ...   
19  [(�, 374), (\

### sentiment analysis 

In [319]:
top_20 = data.sort_values('subreddit').reset_index()

In [320]:
top_20.head()

index   parent_id subreddit_id   subreddit  created_utc          author  \
0  419535   t3_b4ilct     t5_mp3ji  1000ccplus   1553345561    commando-450   
1  422616   t3_b19u1a     t5_mp3ji  1000ccplus   1552637426  megabyteraider   
2   51622  t1_eie1wvy     t5_mp3ji  1000ccplus   1552437482          100men   
3  490129   t3_b43izb     t5_mp3ji  1000ccplus   1553325725   runnersnake72   
4   51625  t1_ejjid48     t5_3e98s  100thieves   1553742677       User8854_   

   score                                               body  
0    -12                                         No thanks   
1    -11           Sorry, but that is Steve Tyler with tits  
2    -14                                       Cute but old  
3     -3  These ladies are good to look at when drunk. I...  
4    -24  I mean they kinda do owe us last year the comm...

In [389]:
temp = sentiment_analyzer_scores(top_20['body'][0])

In [390]:
temp

"{'neg': 0.431, 'neu': 0.0, 'pos': 0.569, 'compound': 0.1779}"

In [452]:
from vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer
analyser = SentimentIntensityAnalyzer()

def sentiment_analyzer_scores(sentence):
    score = analyser.polarity_scores(sentence)
#     print("{}".format(str(score)))
    return score


In [453]:
top_20['senti']= top_20['body'].map(lambda t: sentiment_analyzer_scores(str(t))) 

In [454]:
top_20['senti_pos'] = top_20.senti.apply(lambda x: x.get('pos'))
top_20['senti_neu'] = top_20.senti.apply(lambda x: x.get('neu'))
top_20['senti_neg'] = top_20.senti.apply(lambda x: x.get('neg'))

In [455]:
top_20.head()

index   parent_id subreddit_id   subreddit  created_utc          author  \
0  419535   t3_b4ilct     t5_mp3ji  1000ccplus   1553345561    commando-450   
1  422616   t3_b19u1a     t5_mp3ji  1000ccplus   1552637426  megabyteraider   
2   51622  t1_eie1wvy     t5_mp3ji  1000ccplus   1552437482          100men   
3  490129   t3_b43izb     t5_mp3ji  1000ccplus   1553325725   runnersnake72   
4   51625  t1_ejjid48     t5_3e98s  100thieves   1553742677       User8854_   

   score                                               body  \
0    -12                                         No thanks    
1    -11           Sorry, but that is Steve Tyler with tits   
2    -14                                       Cute but old   
3     -3  These ladies are good to look at when drunk. I...   
4    -24  I mean they kinda do owe us last year the comm...   

                                               senti  senti_pos  senti_neu  \
0  {'neg': 0.431, 'neu': 0.0, 'pos': 0.569, 'comp...      0.569      0.000   
1  {'neg': 0.368, 'neu': 0.632, 'pos': 0.0, 'comp...      0.000      0.632   
2  {'neg': 0.0, 'neu': 0.5, 'pos': 0.5, 'compound...      0.500      0.500   
3  {'neg': 0.139, 'neu': 0.694, 'pos': 0.168, 'co...      0.168      0.694   
4  {'neg': 0.222, 'neu': 0.778, 'pos': 0.0, 'comp...      0.000      0.778   

   senti_neg  
0      0.431  
1      0.368  
2      0.000  
3      0.139  
4      0.222

In [456]:
pd.DataFrame(top_20.groupby('subreddit')['senti_pos'].agg('mean').sort_values(ascending=False).head(20))

senti_pos
subreddit                    
nice                   1.0000
cuckoldstories         1.0000
SolusProject           1.0000
eebooks                1.0000
eu4dadjokes            1.0000
CR10                   1.0000
Jevil                  1.0000
kustom                 1.0000
Mars                   1.0000
unexpectedpawnee       0.8750
Lain                   0.8700
welcometonightvale     0.8510
Opossums               0.8310
GarenMains             0.8095
MilitaryGoneWild       0.8080
dogbridges             0.7960
gifsgonewild           0.7870
Mysteries              0.7700
phgonewild             0.7640
dadsouls               0.7620

In [460]:
pd.DataFrame(top_20.groupby('subreddit')['senti_neg'].agg('mean').sort_values(ascending=False).head(20))

senti_neg
subreddit                     
flags_irl                1.000
Mortytown                1.000
numetal                  1.000
SeriousFIFA              1.000
consolemasterrace        1.000
holdmyturban             1.000
AskRedditNSFW            1.000
YouBelongWithMemes       1.000
adultvrgames             1.000
OldLadiesBakingPies      1.000
hamiltonmemes            1.000
MSsEcReTPoDcAsT          1.000
jaycemains               1.000
snapchat                 1.000
fixedeyebrows            1.000
endia                    0.861
artdoctor                0.795
GayFreeUse               0.787
Wehatedrake              0.778
KimsConvenience          0.778

In [458]:
pd.DataFrame(top_20.groupby('subreddit')['senti_neu'].agg('mean').sort_values(ascending=False).head(20))

senti_neu
subreddit                       
EatingDisorders              1.0
Preacher                     1.0
soapmaking                   1.0
AceOfAngels8                 1.0
greatdanes                   1.0
Portsmouth                   1.0
grammar                      1.0
grailwhores                  1.0
PraiseTheCameraDog           1.0
sololeveling                 1.0
PrehistoricMemes             1.0
thighhighs                   1.0
sonicshowerthoughts          1.0
gonewildcolor                1.0
AustralianShepherd           1.0
sophiedee                    1.0
PressureCooking              1.0
ComfyButts                   1.0
HolyGrailMemes               1.0
PrivateInternetAccess        1.0

In [461]:
pd.DataFrame(top_20.groupby('subreddit')['senti_neu'].agg('mean').sort_values(ascending=False).head(20))

senti_neu
subreddit                       
EatingDisorders              1.0
Preacher                     1.0
soapmaking                   1.0
AceOfAngels8                 1.0
greatdanes                   1.0
Portsmouth                   1.0
grammar                      1.0
grailwhores                  1.0
PraiseTheCameraDog           1.0
sololeveling                 1.0
PrehistoricMemes             1.0
thighhighs                   1.0
sonicshowerthoughts          1.0
gonewildcolor                1.0
AustralianShepherd           1.0
sophiedee                    1.0
PressureCooking              1.0
ComfyButts                   1.0
HolyGrailMemes               1.0
PrivateInternetAccess        1.0

In [463]:
pd.DataFrame(top_20[['subreddit','senti_neg', 'senti_neu', 'senti_pos']]).sample(20)

subreddit  senti_neg  senti_neu  senti_pos
240397      Whatcouldgowrong      0.410      0.361      0.229
21908               AskWomen      0.000      1.000      0.000
180563       ProgrammerHumor      0.000      1.000      0.000
454728            television      0.093      0.907      0.000
120954                Israel      0.000      0.818      0.182
360979                  kpop      0.109      0.783      0.109
418473      quityourbullshit      0.253      0.618      0.129
30726     BlackPeopleTwitter      0.165      0.723      0.112
175898        PoliticalHumor      0.000      1.000      0.000
177170  Political_Revolution      0.000      1.000      0.000
372875                 manga      0.046      0.804      0.150
165454          OutOfTheLoop      0.118      0.815      0.066
466909         todayilearned      0.357      0.643      0.000
454366            television      0.174      0.785      0.041
21768               AskWomen      0.037      0.842      0.121
40268               CHIBears      0.000      0.674      0.326
59405          ConvenientCop      0.091      0.909      0.000
331846             greentext      0.000      0.776      0.224
135857        LivestreamFail      0.147      0.664      0.190
285654            classicwow      0.042      0.833      0.125

In [269]:
def get_sentiment(self, word):
    '''
    Utility function to determine sentiment of passed word 
    using textblob's sentiment method
    '''
    
    # create TextBlob object of passed tweet text 
    analysis = TextBlob(self.clean(word)) 
    
    if analysis.sentiment.polarity > 0:
        return "positive"
    elif analysis.sentiment.polarity ==0:
        return "neutral"
    else:
        return "negative"

### score analysis 

In [441]:
pd.DataFrame(data.groupby('subreddit')['score'].agg('mean').sort_values().head(20))

score
subreddit                   
dillion_harper         -51.0
BlowjobGifs            -41.0
reinhardtrollouts      -38.0
falloutsettlements     -37.0
itrunsdoom             -37.0
P90X                   -37.0
nudism                 -35.0
Moescape               -35.0
voyager                -32.0
fuckingmanly           -32.0
ItsAmateurHour         -31.2
flags_irl              -30.0
AzerothPorn            -29.0
BrieLarson             -29.0
augustames             -28.0
japanesestreetwear     -28.0
UnnecessaryCensorship  -28.0
tacticalgear           -28.0
DeltaRule34            -27.0
unknownvideos          -27.0

In [440]:
pd.DataFrame(data.groupby('subreddit')['score'].agg('mean').sort_values(ascending=False).head(20))

score
subreddit                       
tifu                  264.916331
RoastMe               212.111250
GTAGE                 186.666667
ContagiousLaughter    177.575000
Jokes                 175.128755
gifs                  166.825483
GeometryIsNeat        162.000000
u_SrGrafo             160.181818
HighQualityGifs       156.908046
dadjokes              155.868687
nonononoyes           152.313725
WatchPeopleDieInside  152.011416
Unexpected            149.222008
Simulated             149.190476
therewasanattempt     148.698198
CornGuy               146.000000
WTF                   145.733425
SurgeryGifs           144.000000
justa                 142.000000
blackmagicfuckery     139.950617